<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Functions-to-convert-coordinates" data-toc-modified-id="Functions-to-convert-coordinates-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Functions to convert coordinates</a></span></li><li><span><a href="#GEOPandas" data-toc-modified-id="GEOPandas-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>GEOPandas</a></span></li><li><span><a href="#Population" data-toc-modified-id="Population-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Population</a></span></li><li><span><a href="#Read-in-and-prepare-COVID-data" data-toc-modified-id="Read-in-and-prepare-COVID-data-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Read in and prepare COVID data</a></span></li><li><span><a href="#JSON-conversion" data-toc-modified-id="JSON-conversion-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>JSON conversion</a></span></li><li><span><a href="#Plot-map-function" data-toc-modified-id="Plot-map-function-6"><span class="toc-item-num">6&nbsp;&nbsp;</span>Plot map function</a></span></li><li><span><a href="#Prepare-time-series-data-frames" data-toc-modified-id="Prepare-time-series-data-frames-7"><span class="toc-item-num">7&nbsp;&nbsp;</span>Prepare time series data frames</a></span></li><li><span><a href="#Dashboard" data-toc-modified-id="Dashboard-8"><span class="toc-item-num">8&nbsp;&nbsp;</span>Dashboard</a></span></li><li><span><a href="#Diff-vs-Time" data-toc-modified-id="Diff-vs-Time-9"><span class="toc-item-num">9&nbsp;&nbsp;</span>Diff vs Time</a></span></li></ul></div>

In [360]:
import math

import pandas as pd
import numpy as np

from bokeh.tile_providers import get_provider, Vendors
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, HoverTool, Range1d, GeoJSONDataSource, ColorBar, BasicTicker, Label, LabelSet
from bokeh.io import output_notebook
from bokeh.palettes import Dark2_8, brewer, Viridis, Viridis5, Viridis6, OrRd, Greys256, cividis, gray, viridis, linear_palette, Category10, Category20
from bokeh.models import Legend, LegendItem, LogTicker
from bokeh.core.enums import LegendLocation
import itertools
import seaborn as sns
from bokeh.io import output_notebook, show, output_file
from bokeh.models.mappers import ColorMapper, LinearColorMapper, LogColorMapper
from bokeh.models import Span

import geopandas as gpd
import json

from IPython.display import display  # For showing frames

import panel as pn
# For Bokeh, you can leave this as pn.extension(), but there is no harm in adding vega
#pn.extension('vega')
pn.extension()

# Functions to convert coordinates

In [3]:
# from http://wiki.openstreetmap.org/wiki/Mercator#Java
RADIUS = 6378137.0; # in meters on the equator
def y2lat(aY):
    return math.degrees(math.atan(math.exp(aY / RADIUS)) * 2 - math.pi/2);

def x2lon( aX):
    return math.degrees(aX / RADIUS);
# These functions take their angle parameter in degrees and return a length in meters

def lat2y(a):
    return math.log(math.tan(math.pi / 4 + math.radians(a) / 2)) * RADIUS

def lon2x(a):
    return math.radians(a) * RADIUS

# GEOPandas

In [4]:
shapefile = 'data/ne_110m_admin_0_countries/ne_110m_admin_0_countries.shp'
shapefile2 = 'data/ne_10m_admin_1_states_provinces/ne_10m_admin_1_states_provinces.shp'

gdf = gpd.read_file(shapefile)
#gdf.head()

# gdf2 = gpd.read_file(shapefile2)
#gdf2.head()

In [5]:
# Read shapefile using Geopandas
# [['admin', 'latitude', 'longitude', 'geometry']]#
gdf = gpd.read_file(shapefile)[['ADMIN', 'ADM0_A3', 'geometry']]
# gdf.columns
# Rename columns.
# gdf.columns = ['country', 'latitude', 'longitude', 'geometry']
gdf.columns = ['Country Name', 'Country Code', 'geometry']
# gdf[gdf['admin']=='China']

print(gdf[gdf['Country Name'] == 'Antarctica'])
gdf = gdf.drop(gdf.index[159])
gdf.sort_values(by='Country Name', inplace=True)
# gdf['Country Name'].values

    Country Name Country Code  \
159   Antarctica          ATA   

                                              geometry  
159  MULTIPOLYGON (((-48.66062 -78.04702, -48.15140...  


In [6]:
gdf.shape

(176, 3)

# Population

In [7]:
df_pop = pd.read_csv('./data/API_SPPOPTOTL_DS2_en_csv_v2_821007/API_SPPOPTOTL_DS2_en_csv_v2_821007.csv', header = 2 )
df_pop = df_pop[['Country Name', 'Country Code', '2018']]
df_pop.head()

Country Name Country Code        2018
0        Aruba          ABW    105845.0
1  Afghanistan          AFG  37172386.0
2       Angola          AGO  30809762.0
3      Albania          ALB   2866376.0
4      Andorra          AND     77006.0

In [8]:
df_pop.shape

(264, 3)

In [9]:
missing_pop_in_map=gdf.loc[~gdf['Country Code'].isin(df_pop['Country Code']), ['Country Name']].values.flatten()
print(missing_pop_in_map)
missing_code_pop_in_map=gdf.loc[~gdf['Country Code'].isin(df_pop['Country Code']), ['Country Code']].values.flatten()
print(missing_code_pop_in_map)
#for c in missing_pop_in_map:
#    print(gdf.loc[gdf['Country Name']==c, ['Country Code', 'Country Name']])

['Falkland Islands' 'French Southern and Antarctic Lands' 'Kosovo'
 'Northern Cyprus' 'Palestine' 'Somaliland' 'South Sudan' 'Taiwan'
 'Western Sahara']
['FLK' 'ATF' 'KOS' 'CYN' 'PSX' 'SOL' 'SDS' 'TWN' 'SAH']


In [10]:
countrycodes=df_pop['Country Code'].values
print(countrycodes)

['ABW' 'AFG' 'AGO' 'ALB' 'AND' 'ARB' 'ARE' 'ARG' 'ARM' 'ASM' 'ATG' 'AUS'
 'AUT' 'AZE' 'BDI' 'BEL' 'BEN' 'BFA' 'BGD' 'BGR' 'BHR' 'BHS' 'BIH' 'BLR'
 'BLZ' 'BMU' 'BOL' 'BRA' 'BRB' 'BRN' 'BTN' 'BWA' 'CAF' 'CAN' 'CEB' 'CHE'
 'CHI' 'CHL' 'CHN' 'CIV' 'CMR' 'COD' 'COG' 'COL' 'COM' 'CPV' 'CRI' 'CSS'
 'CUB' 'CUW' 'CYM' 'CYP' 'CZE' 'DEU' 'DJI' 'DMA' 'DNK' 'DOM' 'DZA' 'EAP'
 'EAR' 'EAS' 'ECA' 'ECS' 'ECU' 'EGY' 'EMU' 'ERI' 'ESP' 'EST' 'ETH' 'EUU'
 'FCS' 'FIN' 'FJI' 'FRA' 'FRO' 'FSM' 'GAB' 'GBR' 'GEO' 'GHA' 'GIB' 'GIN'
 'GMB' 'GNB' 'GNQ' 'GRC' 'GRD' 'GRL' 'GTM' 'GUM' 'GUY' 'HIC' 'HKG' 'HND'
 'HPC' 'HRV' 'HTI' 'HUN' 'IBD' 'IBT' 'IDA' 'IDB' 'IDN' 'IDX' 'IMN' 'IND'
 'INX' 'IRL' 'IRN' 'IRQ' 'ISL' 'ISR' 'ITA' 'JAM' 'JOR' 'JPN' 'KAZ' 'KEN'
 'KGZ' 'KHM' 'KIR' 'KNA' 'KOR' 'KWT' 'LAC' 'LAO' 'LBN' 'LBR' 'LBY' 'LCA'
 'LCN' 'LDC' 'LIC' 'LIE' 'LKA' 'LMC' 'LMY' 'LSO' 'LTE' 'LTU' 'LUX' 'LVA'
 'MAC' 'MAF' 'MAR' 'MCO' 'MDA' 'MDG' 'MDV' 'MEA' 'MEX' 'MHL' 'MIC' 'MKD'
 'MLI' 'MLT' 'MMR' 'MNA' 'MNE' 'MNG' 'MNP' 'MOZ' 'M

# Read in and prepare COVID data

In [11]:
def read_covid_df(name):
    filename = f"./data/csse_covid_19_data/csse_covid_19_time_series/time_series_19-covid-{name}.csv"
    df = pd.read_csv(filename)
    df = df.set_index(['Province/State', 'Country/Region', 'Lat', 'Long'])
    df.columns = pd.to_datetime(df.columns)
    return df

def summarize_df(df, name):
    ser = df.groupby(level='Country/Region').sum().iloc[:,-1].sort_values(ascending=False)
    ser.name = f"Total {name}"
    return ser

In [12]:
confirmed_df = read_covid_df("Confirmed")
deaths_df = read_covid_df("Deaths")
recovered_df = read_covid_df("Recovered")

In [430]:
confirmed_ser = summarize_df(confirmed_df, "Confirmed")
deaths_ser = summarize_df(deaths_df, "Deaths")
recovered_ser = summarize_df(recovered_df, "Recovered")

In [13]:
confirmed_df.head()

2020-01-22  2020-01-23  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000           2           3   
               Japan          36.0000 138.0000           2           1   
               Singapore      1.2833  103.8333           0           1   
               Nepal          28.1667 84.2500            0           0   
               Malaysia       2.5000  112.5000           0           0   

                                                2020-01-24  2020-01-25  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000           5           7   
               Japan          36.0000 138.0000           2           2   
               Singapore      1.2833  103.8333           3           3   
               Nepal          28.1667 84.2500            0           1   
               Malaysia       2.5000  112.5000           0           3   

                                                2020-01-26  2020-01-27  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000           8           8   
               Japan          36.0000 138.0000           4           4   
               Singapore      1.2833  103.8333           4           5   
               Nepal          28.1667 84.2500            1           1   
               Malaysia       2.5000  112.5000           4           4   

                                                2020-01-28  2020-01-29  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000          14          14   
               Japan          36.0000 138.0000           7           7   
               Singapore      1.2833  103.8333           7           7   
               Nepal          28.1667 84.2500            1           1   
               Malaysia       2.5000  112.5000           4           7   

                                                2020-01-30  2020-01-31  ...  \
Province/State Country/Region Lat     Long                              ...   
NaN            Thailand       15.0000 101.0000          14          19  ...   
               Japan          36.0000 138.0000          11          15  ...   
               Singapore      1.2833  103.8333          10          13  ...   
               Nepal          28.1667 84.2500            1           1  ...   
               Malaysia       2.5000  112.5000           8           8  ...   

                                                2020-03-04  2020-03-05  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000          43          47   
               Japan          36.0000 138.0000         331         360   
               Singapore      1.2833  103.8333         110         117   
               Nepal          28.1667 84.2500            1           1   
               Malaysia       2.5000  112.5000          50          50   

                                                2020-03-06  2020-03-07  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000          48          50   
               Japan          36.0000 138.0000         420         461   
               Singapore      1.2833  103.8333         130         138   
               Nepal          28.1667 84.2500            1           1   
               Malaysia       2.5000  112.5000          83          93   

                                                2020-03-08  2020-03-09  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000          50          50   
               Japan          36.0000 138.0000         502         511   
               Singapore      1.2833  103.8333         150         150   
          

In [14]:
tser = confirmed_df.iloc[:,-1]
tser.name = "Confirmed"
tdf = tser.reset_index()

# Add in deaths
tser = deaths_df.iloc[:,-1]
tser.name = "Deaths"
map_df = tdf.join(tser.reset_index(drop=True))

# Add in Recovered
tser = recovered_df.iloc[:,-1]
tser.name = "Recovered"
map_df = map_df.join(tser.reset_index(drop=True))

map_df['X'] = map_df['Long'].apply(lambda x: lon2x(x))
map_df['Y'] = map_df['Lat'].apply(lambda x: lat2y(x))
map_df.head()

Province/State Country/Region      Lat      Long  Confirmed  Deaths  \
0            NaN       Thailand  15.0000  101.0000         75       1   
1            NaN          Japan  36.0000  138.0000        701      19   
2            NaN      Singapore   1.2833  103.8333        200       0   
3            NaN          Nepal  28.1667   84.2500          1       0   
4            NaN       Malaysia   2.5000  112.5000        197       0   

   Recovered             X             Y  
0         35  1.124327e+07  1.689200e+06  
1        118  1.536209e+07  4.300621e+06  
2         97  1.155867e+07  1.428682e+05  
3          1  9.378667e+06  3.270007e+06  
4         26  1.252344e+07  2.783871e+05

In [15]:
map_df['Size'] = np.log1p(map_df['Confirmed']) * 1.5

In [18]:
map_df['Size'].max()

16.686188572696448

In [19]:
map_df_gr_country = map_df[['Country/Region', 'Confirmed', 'Deaths', 'Recovered']]
map_df_gr_country = map_df_gr_country.groupby('Country/Region').sum().reset_index()
map_df_gr_country.sort_values(by='Country/Region', inplace=True)
map_df_gr_country.head()

Country/Region  Confirmed  Deaths  Recovered
0          Afghanistan          7       0          0
1              Albania         33       1          0
2              Algeria         26       2          8
3              Andorra          1       0          0
4  Antigua and Barbuda          1       0          0

In [20]:
missing_countries_cov = map_df_gr_country.loc[~map_df_gr_country['Country/Region'].isin(df_pop['Country Name']), ['Country/Region']].values.flatten()
print(missing_countries_cov)

['Brunei' 'Congo (Kinshasa)' 'Cruise Ship' 'Czechia' 'Egypt'
 'French Guiana' 'Guadeloupe' 'Holy See' 'Iran' 'Korea, South'
 'Martinique' 'Reunion' 'Russia' 'Slovakia' 'Taiwan*' 'US']


In [21]:
missing_countries_cov_ = df_pop.loc[~df_pop['Country Name'].isin(map_df_gr_country['Country/Region']), ['Country Code']].values.flatten()
print(missing_countries_cov_)

['AGO' 'ARB' 'ASM' 'BDI' 'BEN' 'BHS' 'BLZ' 'BMU' 'BRB' 'BRN' 'BWA' 'CAF'
 'CEB' 'CHI' 'COD' 'COG' 'COM' 'CPV' 'CSS' 'CUW' 'CZE' 'DJI' 'DMA' 'EAP'
 'EAR' 'EAS' 'ECA' 'ECS' 'EGY' 'EMU' 'ERI' 'EUU' 'FCS' 'FJI' 'FRO' 'FSM'
 'GAB' 'GHA' 'GIB' 'GMB' 'GNB' 'GNQ' 'GRD' 'GRL' 'GTM' 'GUM' 'HIC' 'HKG'
 'HPC' 'HTI' 'IBD' 'IBT' 'IDA' 'IDB' 'IDX' 'IMN' 'INX' 'IRN' 'KGZ' 'KIR'
 'KNA' 'KOR' 'LAC' 'LAO' 'LBR' 'LBY' 'LCA' 'LCN' 'LDC' 'LIC' 'LMC' 'LMY'
 'LSO' 'LTE' 'MAC' 'MAF' 'MDG' 'MEA' 'MHL' 'MIC' 'MLI' 'MMR' 'MNA' 'MNE'
 'MNP' 'MOZ' 'MRT' 'MUS' 'MWI' 'NAC' 'NAM' 'NCL' 'NER' 'NIC' 'NRU' 'OED'
 'OSS' 'PLW' 'PNG' 'PRE' 'PRI' 'PRK' 'PSE' 'PSS' 'PST' 'PYF' 'RUS' 'RWA'
 'SAS' 'SLB' 'SLE' 'SLV' 'SOM' 'SSA' 'SSD' 'SSF' 'SST' 'STP' 'SUR' 'SVK'
 'SWZ' 'SXM' 'SYC' 'SYR' 'TCA' 'TCD' 'TEA' 'TEC' 'TJK' 'TKM' 'TLA' 'TLS'
 'TMN' 'TON' 'TSA' 'TSS' 'TTO' 'TUV' 'TZA' 'UGA' 'UMC' 'URY' 'USA' 'UZB'
 'VCT' 'VEN' 'VGB' 'VIR' 'VUT' 'WLD' 'WSM' 'XKX' 'YEM' 'ZMB' 'ZWE']


In [22]:
sorted(map_df_gr_country['Country/Region'].values)

['Afghanistan',
 'Albania',
 'Algeria',
 'Andorra',
 'Antigua and Barbuda',
 'Argentina',
 'Armenia',
 'Aruba',
 'Australia',
 'Austria',
 'Azerbaijan',
 'Bahrain',
 'Bangladesh',
 'Belarus',
 'Belgium',
 'Bhutan',
 'Bolivia',
 'Bosnia and Herzegovina',
 'Brazil',
 'Brunei',
 'Bulgaria',
 'Burkina Faso',
 'Cambodia',
 'Cameroon',
 'Canada',
 'Cayman Islands',
 'Chile',
 'China',
 'Colombia',
 'Congo (Kinshasa)',
 'Costa Rica',
 "Cote d'Ivoire",
 'Croatia',
 'Cruise Ship',
 'Cuba',
 'Cyprus',
 'Czechia',
 'Denmark',
 'Dominican Republic',
 'Ecuador',
 'Egypt',
 'Estonia',
 'Ethiopia',
 'Finland',
 'France',
 'French Guiana',
 'Georgia',
 'Germany',
 'Greece',
 'Guadeloupe',
 'Guinea',
 'Guyana',
 'Holy See',
 'Honduras',
 'Hungary',
 'Iceland',
 'India',
 'Indonesia',
 'Iran',
 'Iraq',
 'Ireland',
 'Israel',
 'Italy',
 'Jamaica',
 'Japan',
 'Jordan',
 'Kazakhstan',
 'Kenya',
 'Korea, South',
 'Kuwait',
 'Latvia',
 'Lebanon',
 'Liechtenstein',
 'Lithuania',
 'Luxembourg',
 'Malaysia',
 '

In [20]:
sorted(df_pop['Country Name'].values)

['Afghanistan',
 'Albania',
 'Algeria',
 'American Samoa',
 'Andorra',
 'Angola',
 'Antigua and Barbuda',
 'Arab World',
 'Argentina',
 'Armenia',
 'Aruba',
 'Australia',
 'Austria',
 'Azerbaijan',
 'Bahamas, The',
 'Bahrain',
 'Bangladesh',
 'Barbados',
 'Belarus',
 'Belgium',
 'Belize',
 'Benin',
 'Bermuda',
 'Bhutan',
 'Bolivia',
 'Bosnia and Herzegovina',
 'Botswana',
 'Brazil',
 'British Virgin Islands',
 'Brunei Darussalam',
 'Bulgaria',
 'Burkina Faso',
 'Burundi',
 'Cabo Verde',
 'Cambodia',
 'Cameroon',
 'Canada',
 'Caribbean small states',
 'Cayman Islands',
 'Central African Republic',
 'Central Europe and the Baltics',
 'Chad',
 'Channel Islands',
 'Chile',
 'China',
 'Colombia',
 'Comoros',
 'Congo, Dem. Rep.',
 'Congo, Rep.',
 'Costa Rica',
 "Cote d'Ivoire",
 'Croatia',
 'Cuba',
 'Curacao',
 'Cyprus',
 'Czech Republic',
 'Denmark',
 'Djibouti',
 'Dominica',
 'Dominican Republic',
 'Early-demographic dividend',
 'East Asia & Pacific',
 'East Asia & Pacific (IDA & IBRD coun

In [23]:
def rename_countries(data):
    df=data.copy()
    df.loc[df['Country/Region']=='Brunei', ['Country/Region']]='Brunei Darussalam'
    df.loc[df['Country/Region']=='Congo (Kinshasa)', ['Country/Region']]='Congo, Dem. Rep.'
    df.loc[df['Country/Region']=='Czechia', ['Country/Region']]='Czech Republic'
    df.loc[df['Country/Region']=='French Guiana', ['Country/Region']]='French Guyana'
    df.loc[df['Country/Region']=='Egypt', ['Country/Region']]='Egypt, Arab Rep.'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Guadeloupe', ['Country/Region']]=''
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Holy See', ['Country/Region']]=''
    df.loc[df['Country/Region']=='Iran', ['Country/Region']]='Iran, Islamic Rep.'
    df.loc[df['Country/Region']=='Korea, South', ['Country/Region']]='Korea, Rep.'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Martinique', ['Country/Region']]=''
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Reunion', ['Country/Region']]=''
    df.loc[df['Country/Region']=='Russia', ['Country/Region']]='Russian Federation'
    df.loc[df['Country/Region']=='Slovakia', ['Country/Region']]='Slovak Republic'
    df.loc[df['Country/Region']=='Taiwan*', ['Country/Region']]='Taiwan'
    df.loc[df['Country/Region']=='US', ['Country/Region']]='United States'
    
    #remove 'Criuse Ship' country
    #df.drop(df.loc[df['Country/Region']=='Cruise Ship'].index, inplace=True)
    return df

def merge_with_population(df, df_pop):
    df_merged = pd.merge(df, df_pop, left_on='Country/Region', right_on='Country Name', how='left')
    df_merged.loc[df_merged['Country/Region']=='Guadeloupe', ['2018']]=395700.
    df_merged.loc[df_merged['Country/Region']=='Holy See', ['2018']]= 1000.
    df_merged.loc[df_merged['Country/Region']=='Martinique', ['2018']]=376480.
    df_merged.loc[df_merged['Country/Region']=='Reunion', ['2018']]=859959.
    df_merged.loc[df_merged['Country/Region']=='Taiwan', ['2018']]=23216236.
    df_merged.loc[df_merged['Country/Region']=='Cruise Ship', ['2018']]=1000.
    df_merged.loc[df_merged['Country/Region']=='French Guyana', ['2018']]=255455.
    df_merged.loc[df_merged['Country/Region']=='Guadeloupe', ['Country Name']]='Guadeloupe'
    df_merged.loc[df_merged['Country/Region']=='Holy See', ['Country Name']]= 'Holy See'
    df_merged.loc[df_merged['Country/Region']=='Martinique', ['Country Name']]='Martinique'
    df_merged.loc[df_merged['Country/Region']=='Reunion', ['Country Name']]='Reunion'
    df_merged.loc[df_merged['Country/Region']=='Taiwan', ['Country Name']]='Taiwan'
    df_merged.loc[df_merged['Country/Region']=='Cruise Ship', ['Country Name']]='Cruise Ship'
    df_merged.loc[df_merged['Country/Region']=='French Guyana', ['Country Name']]='French Guyana'
    df_merged.loc[df_merged['Country/Region']=='Guadeloupe', ['Country Code']]='GLP'
    df_merged.loc[df_merged['Country/Region']=='Holy See', ['Country Code']]= 'VAT'
    df_merged.loc[df_merged['Country/Region']=='Martinique', ['Country Code']]='MTQ'
    df_merged.loc[df_merged['Country/Region']=='Reunion', ['Country Code']]='REU'
    df_merged.loc[df_merged['Country/Region']=='Taiwan', ['Country Code']]='TWN'
    df_merged.loc[df_merged['Country/Region']=='Cruise Ship', ['Country Code']]='cruise'
    df_merged.loc[df_merged['Country/Region']=='French Guyana', ['Country Code']]='GUF'
    return df_merged

# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Brunei', ['Country/Region']]='Brunei Darussalam'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Congo (Kinshasa)', ['Country/Region']]='Congo, Dem. Rep.'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Czechia', ['Country/Region']]='Czech Republic'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='French Guiana', ['Country/Region']]='Guyana'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Guadeloupe', ['Country/Region']]=''
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Holy See', ['Country/Region']]=''
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Iran', ['Country/Region']]='Iran, Islamic Rep.'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Korea, South', ['Country/Region']]='Korea, Rep.'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Martinique', ['Country/Region']]=''
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Reunion', ['Country/Region']]=''
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Russia', ['Country/Region']]='Russian Federation'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Slovakia', ['Country/Region']]='Slovak Republic'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Taiwan*', ['Country/Region']]='Taiwan'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='US', ['Country/Region']]='United States'


# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Mainland China', ['Country/Region']]='China'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Iran (Islamic Republic of)', ['Country/Region']]='Iran'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Republic of Korea', ['Country/Region']]='South Korea'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='US', ['Country/Region']]='United States of America'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='UK', ['Country/Region']]='United Kingdom'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Czech Republic', ['Country/Region']]='Czechia'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Russian Federation', ['Country/Region']]='Russia'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='North Macedonia', ['Country/Region']]='Macedonia'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Republic of Moldova', ['Country/Region']]='Moldova'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Viet Nam', ['Country/Region']]='Vietnam'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='occupied Palestinian territory', ['Country/Region']]='Palestine'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='French Guiana', ['Country/Region']]='Guyana'
# map_df_gr_country.loc[map_df_gr_country['Country/Region']=='Serbia', ['Country/Region']]='Republic of Serbia'
# print(map_df_gr_country.head())
# print(len(map_df_gr_country['Country/Region']))
#print(map_df_gr_country['Country/Region'].values)

In [24]:
print(map_df_gr_country.head())
map_df_gr_country_rename = rename_countries(map_df_gr_country)
print(map_df_gr_country_rename.head())

        Country/Region  Confirmed  Deaths  Recovered
0          Afghanistan          7       0          0
1              Albania         33       1          0
2              Algeria         26       2          8
3              Andorra          1       0          0
4  Antigua and Barbuda          1       0          0
        Country/Region  Confirmed  Deaths  Recovered
0          Afghanistan          7       0          0
1              Albania         33       1          0
2              Algeria         26       2          8
3              Andorra          1       0          0
4  Antigua and Barbuda          1       0          0


In [25]:
missing_countries_cov = map_df_gr_country_rename.loc[~map_df_gr_country_rename['Country/Region'].isin(df_pop['Country Name']), ['Country/Region']].values.flatten()
print(missing_countries_cov)

['Cruise Ship' 'French Guyana' 'Guadeloupe' 'Holy See' 'Martinique'
 'Reunion' 'Taiwan']


In [26]:
print(map_df_gr_country_rename.shape)
print(df_pop.shape)
map_df_gr_country_population = merge_with_population(map_df_gr_country_rename, df_pop)
print(map_df_gr_country_population.shape)

(125, 4)
(264, 3)
(125, 7)


In [27]:
map_df_gr_country_population.isna().sum()

Country/Region    0
Confirmed         0
Deaths            0
Recovered         0
Country Name      0
Country Code      0
2018              0
dtype: int64

In [28]:
map_df_gr_country_population.head()

Country/Region  Confirmed  Deaths  Recovered         Country Name  \
0          Afghanistan          7       0          0          Afghanistan   
1              Albania         33       1          0              Albania   
2              Algeria         26       2          8              Algeria   
3              Andorra          1       0          0              Andorra   
4  Antigua and Barbuda          1       0          0  Antigua and Barbuda   

  Country Code        2018  
0          AFG  37172386.0  
1          ALB   2866376.0  
2          DZA  42228429.0  
3          AND     77006.0  
4          ATG     96286.0

In [29]:
map_df_gr_country_population.loc[map_df_gr_country_population['2018']<100000, ['Country Name', '2018']]

Country Name     2018
3                Andorra  77006.0
4    Antigua and Barbuda  96286.0
25        Cayman Islands  64174.0
33           Cruise Ship   1000.0
52              Holy See   1000.0
72         Liechtenstein  37910.0
81                Monaco  38682.0
102           San Marino  33785.0

In [30]:
missing_countries_cov__ = map_df_gr_country_population.loc[~map_df_gr_country_population['Country Code'].isin(gdf['Country Code']), ['Country/Region']].values.flatten()
print(missing_countries_cov__)

['Andorra' 'Antigua and Barbuda' 'Aruba' 'Bahrain' 'Cayman Islands'
 'Cruise Ship' 'French Guyana' 'Guadeloupe' 'Holy See' 'Liechtenstein'
 'Maldives' 'Malta' 'Martinique' 'Monaco' 'Reunion' 'San Marino'
 'Singapore']


In [31]:

map_df_gr_country_population.loc[map_df_gr_country_population['Confirmed']==0]

Empty DataFrame
Columns: [Country/Region, Confirmed, Deaths, Recovered, Country Name, Country Code, 2018]
Index: []

In [32]:
# add columns cases/population
map_df_gr_country_population['ConfirmedDensityPerc'] = 100000.*map_df_gr_country_population['Confirmed']/map_df_gr_country_population['2018']
map_df_gr_country_population['DeathsDensityPerc'] = 100000.*map_df_gr_country_population['Deaths']/map_df_gr_country_population['2018']
map_df_gr_country_population['RecoveredDensityPerc'] = 100000.*map_df_gr_country_population['Recovered']/map_df_gr_country_population['2018']
map_df_gr_country_population['ConfirmedDensityLog'] = 100*np.log1p(map_df_gr_country_population['Confirmed']/map_df_gr_country_population['2018'])
map_df_gr_country_population['DeathsDensityLog'] = 100*np.log1p(map_df_gr_country_population['Deaths']/map_df_gr_country_population['2018'])
map_df_gr_country_population['RecoveredDensityLog'] = 100*np.log1p(map_df_gr_country_population['Recovered']/map_df_gr_country_population['2018'])

In [33]:
map_df_gr_country_population.head()

Country/Region  Confirmed  Deaths  Recovered         Country Name  \
0          Afghanistan          7       0          0          Afghanistan   
1              Albania         33       1          0              Albania   
2              Algeria         26       2          8              Algeria   
3              Andorra          1       0          0              Andorra   
4  Antigua and Barbuda          1       0          0  Antigua and Barbuda   

  Country Code        2018  ConfirmedDensityPerc  DeathsDensityPerc  \
0          AFG  37172386.0              0.018831           0.000000   
1          ALB   2866376.0              1.151280           0.034887   
2          DZA  42228429.0              0.061570           0.004736   
3          AND     77006.0              1.298600           0.000000   
4          ATG     96286.0              1.038573           0.000000   

   RecoveredDensityPerc  ConfirmedDensityLog  DeathsDensityLog  \
0              0.000000             0.000019          0.000000   
1              0.000000             0.001151          0.000035   
2              0.018945             0.000062          0.000005   
3              0.000000             0.001299          0.000000   
4              0.000000             0.001039          0.000000   

   RecoveredDensityLog  
0             0.000000  
1             0.000000  
2             0.000019  
3             0.000000  
4             0.000000

In [34]:
map_df_gr_country_population['ConfirmedDensityLog'].max()

52.82725373697112

In [35]:
map_df_gr_country_population['ConfirmedDensityLog'].min()

9.155450061577039e-07

In [36]:
# check coordinates df and cases df country codes
missing_countries_cod = map_df_gr_country_population.loc[~map_df_gr_country_population['Country Code'].isin(gdf['Country Code']), ['Country/Region']].values.flatten()
print(missing_countries_cod)

['Andorra' 'Antigua and Barbuda' 'Aruba' 'Bahrain' 'Cayman Islands'
 'Cruise Ship' 'French Guyana' 'Guadeloupe' 'Holy See' 'Liechtenstein'
 'Maldives' 'Malta' 'Martinique' 'Monaco' 'Reunion' 'San Marino'
 'Singapore']


In [37]:
sorted(gdf['Country Name'].values)

['Afghanistan',
 'Albania',
 'Algeria',
 'Angola',
 'Argentina',
 'Armenia',
 'Australia',
 'Austria',
 'Azerbaijan',
 'Bangladesh',
 'Belarus',
 'Belgium',
 'Belize',
 'Benin',
 'Bhutan',
 'Bolivia',
 'Bosnia and Herzegovina',
 'Botswana',
 'Brazil',
 'Brunei',
 'Bulgaria',
 'Burkina Faso',
 'Burundi',
 'Cambodia',
 'Cameroon',
 'Canada',
 'Central African Republic',
 'Chad',
 'Chile',
 'China',
 'Colombia',
 'Costa Rica',
 'Croatia',
 'Cuba',
 'Cyprus',
 'Czechia',
 'Democratic Republic of the Congo',
 'Denmark',
 'Djibouti',
 'Dominican Republic',
 'East Timor',
 'Ecuador',
 'Egypt',
 'El Salvador',
 'Equatorial Guinea',
 'Eritrea',
 'Estonia',
 'Ethiopia',
 'Falkland Islands',
 'Fiji',
 'Finland',
 'France',
 'French Southern and Antarctic Lands',
 'Gabon',
 'Gambia',
 'Georgia',
 'Germany',
 'Ghana',
 'Greece',
 'Greenland',
 'Guatemala',
 'Guinea',
 'Guinea-Bissau',
 'Guyana',
 'Haiti',
 'Honduras',
 'Hungary',
 'Iceland',
 'India',
 'Indonesia',
 'Iran',
 'Iraq',
 'Ireland',
 'I

In [36]:
gdf.shape

(176, 3)

In [38]:
len(gdf['Country Code'].unique())

176

In [39]:
map_df_gr_country_population.shape

(125, 13)

In [40]:
map_df_gr_country_population.loc[map_df_gr_country_population['Country Code']=='GUY']

Country/Region  Confirmed  Deaths  Recovered Country Name Country Code  \
51         Guyana          1       1          0       Guyana          GUY   

        2018  ConfirmedDensityPerc  DeathsDensityPerc  RecoveredDensityPerc  \
51  779004.0              0.128369           0.128369                   0.0   

    ConfirmedDensityLog  DeathsDensityLog  RecoveredDensityLog  
51             0.000128          0.000128                  0.0

In [41]:
sorted(map_df_gr_country_population['ConfirmedDensityPerc'].values)

[0.0009155450103488172,
 0.0010210607044073166,
 0.0018592424669026488,
 0.0019457899041134194,
 0.0023790239271639937,
 0.002392256762449358,
 0.0035602555992940866,
 0.003988953948284568,
 0.006062320680250815,
 0.006073878478990042,
 0.00672306330732225,
 0.007931397535643403,
 0.008055214954216575,
 0.00950941046504916,
 0.010044183358174273,
 0.010125795286290408,
 0.012675726769132171,
 0.013194164428410184,
 0.01883118291088444,
 0.019428719055115888,
 0.02086044756924678,
 0.021886029704047804,
 0.025778642495565374,
 0.026183976473898554,
 0.026424403041906814,
 0.02768804799261652,
 0.030769613259192516,
 0.031146599777613276,
 0.031543671582432445,
 0.03527916135788786,
 0.04153713570504148,
 0.047049236555563034,
 0.049193851459374854,
 0.06000829502163121,
 0.06156989643161956,
 0.0630741322891621,
 0.06967152930490153,
 0.07208692453324421,
 0.0812813228372729,
 0.08625558882305831,
 0.08752938799201831,
 0.09950623251434046,
 0.10234367004400778,
 0.10802476515272023,
 0

In [42]:
map_df_gr_country_population.loc[map_df_gr_country_population['ConfirmedDensityPerc']<0.01]

Country/Region  Confirmed  Deaths  Recovered      Country Name  \
12         Bangladesh          3       0          0        Bangladesh   
23           Cameroon          2       0          0          Cameroon   
29   Congo, Dem. Rep.          2       0          0  Congo, Dem. Rep.   
31      Cote d'Ivoire          1       0          0     Cote d'Ivoire   
42           Ethiopia          1       0          0          Ethiopia   
50             Guinea          1       0          0            Guinea   
56              India         82       2          4             India   
67              Kenya          1       0          0             Kenya   
79             Mexico         12       0          4            Mexico   
84              Nepal          1       0          1             Nepal   
87            Nigeria          2       0          0           Nigeria   
112             Sudan          1       1          0             Sudan   
119            Turkey          5       0          0            Turkey   
121           Ukraine          3       1          0           Ukraine   

    Country Code          2018  ConfirmedDensityPerc  DeathsDensityPerc  \
12           BGD  1.613560e+08              0.001859           0.000000   
23           CMR  2.521624e+07              0.007931           0.000000   
29           COD  8.406809e+07              0.002379           0.000000   
31           CIV  2.506923e+07              0.003989           0.000000   
42           ETH  1.092246e+08              0.000916           0.000000   
50           GIN  1.241432e+07              0.008055           0.000000   
56           IND  1.352617e+09              0.006062           0.000148   
67           KEN  5.139301e+07              0.001946           0.000000   
79           MEX  1.261908e+08              0.009509           0.000000   
84           NPL  2.808787e+07              0.003560           0.000000   
87           NGA  1.958747e+08              0.001021           0.000000   
112          SDN  4.180153e+07              0.002392           0.002392   
119          TUR  8.231972e+07              0.006074           0.000000   
121          UKR  4.462252e+07              0.006723           0.002241   

     RecoveredDensityPerc  ConfirmedDensityLog  DeathsDensityLog  \
12               0.000000         1.859242e-06      0.000000e+00   
23               0.000000         7.931397e-06      0.000000e+00   
29               0.000000         2.379024e-06      0.000000e+00   
31               0.000000         3.988954e-06      0.000000e+00   
42               0.000000         9.155450e-07      0.000000e+00   
50               0.000000         8.055215e-06      0.000000e+00   
56               0.000296         6.062320e-06      1.478615e-07   
67               0.000000         1.945790e-06      0.000000e+00   
79               0.003170         9.509410e-06      0.000000e+00   
84               0.003560         3.560256e-06      0.000000e+00   
87               0.000000         1.021061e-06      0.000000e+00   
112              0.000000         2.392257e-06      2.392257e-06   
119              0.000000         6.073878e-06      0.000000e+00   
121              0.000000         6.723063e-06      2.241021e-06   

     RecoveredDensityLog  
12          0.000000e+00  
23          0.000000e+00  
29          0.000000e+00  
31          0.000000e+00  
42          0.000000e+00  
50          0.000000e+00  
56          2.957230e-07  
67          0.000000e+00  
79          3.169803e-06  
84          3.560256e-06  
87          0.000000e+00  
112         0.000000e+00  
119         0.000000e+00  
121         0.000000e+00

In [161]:
# merge data frames

#map_color_df = pd.merge(map_df_gr_country_population, gdf, left_on='Country Code', right_on='Country Code', how='right')
map_color_df = pd.merge(gdf, map_df_gr_country_population, left_on='Country Code', right_on='Country Code', how='left')

In [162]:
map_color_df.shape

(176, 15)

In [163]:
map_color_df = map_color_df[['Country Name_x', 'Country Code', 'geometry',
       'Confirmed', 'Deaths', 'Recovered', '2018',
       'ConfirmedDensityPerc', 'DeathsDensityPerc', 'RecoveredDensityPerc','ConfirmedDensityLog', 'DeathsDensityLog', 'RecoveredDensityLog']]
map_color_df.head()

Country Name_x Country Code  \
0    Afghanistan          AFG   
1        Albania          ALB   
2        Algeria          DZA   
3         Angola          AGO   
4      Argentina          ARG   

                                            geometry  Confirmed  Deaths  \
0  POLYGON ((66.51861 37.36278, 67.07578 37.35614...        7.0     0.0   
1  POLYGON ((21.02004 40.84273, 20.99999 40.58000...       33.0     1.0   
2  POLYGON ((-8.68440 27.39574, -8.66512 27.58948...       26.0     2.0   
3  MULTIPOLYGON (((12.99552 -4.78110, 12.63161 -4...        NaN     NaN   
4  MULTIPOLYGON (((-68.63401 -52.63637, -68.25000...       31.0     2.0   

   Recovered        2018  ConfirmedDensityPerc  DeathsDensityPerc  \
0        0.0  37172386.0              0.018831           0.000000   
1        0.0   2866376.0              1.151280           0.034887   
2        8.0  42228429.0              0.061570           0.004736   
3        NaN         NaN                   NaN                NaN   
4        0.0  44494502.0              0.069672           0.004495   

   RecoveredDensityPerc  ConfirmedDensityLog  DeathsDensityLog  \
0              0.000000             0.000019          0.000000   
1              0.000000             0.001151          0.000035   
2              0.018945             0.000062          0.000005   
3                   NaN                  NaN               NaN   
4              0.000000             0.000070          0.000004   

   RecoveredDensityLog  
0             0.000000  
1             0.000000  
2             0.000019  
3                  NaN  
4             0.000000

In [46]:
map_color_df.loc[map_color_df['Country Name_x']=='San Marino']

Empty GeoDataFrame
Columns: [Country Name_x, Country Code, geometry, Confirmed, Deaths, Recovered, 2018, ConfirmedDensityPerc, DeathsDensityPerc, RecoveredDensityPerc, ConfirmedDensityLog, DeathsDensityLog, RecoveredDensityLog]
Index: []

In [164]:
#map_color_df.fillna('No data', inplace=True)
map_color_df.fillna(0, inplace=True)
map_color_df.head()

Country Name_x Country Code  \
0    Afghanistan          AFG   
1        Albania          ALB   
2        Algeria          DZA   
3         Angola          AGO   
4      Argentina          ARG   

                                            geometry  Confirmed  Deaths  \
0  POLYGON ((66.51861 37.36278, 67.07578 37.35614...        7.0     0.0   
1  POLYGON ((21.02004 40.84273, 20.99999 40.58000...       33.0     1.0   
2  POLYGON ((-8.68440 27.39574, -8.66512 27.58948...       26.0     2.0   
3  MULTIPOLYGON (((12.99552 -4.78110, 12.63161 -4...        0.0     0.0   
4  MULTIPOLYGON (((-68.63401 -52.63637, -68.25000...       31.0     2.0   

   Recovered        2018  ConfirmedDensityPerc  DeathsDensityPerc  \
0        0.0  37172386.0              0.018831           0.000000   
1        0.0   2866376.0              1.151280           0.034887   
2        8.0  42228429.0              0.061570           0.004736   
3        0.0         0.0              0.000000           0.000000   
4        0.0  44494502.0              0.069672           0.004495   

   RecoveredDensityPerc  ConfirmedDensityLog  DeathsDensityLog  \
0              0.000000             0.000019          0.000000   
1              0.000000             0.001151          0.000035   
2              0.018945             0.000062          0.000005   
3              0.000000             0.000000          0.000000   
4              0.000000             0.000070          0.000004   

   RecoveredDensityLog  
0             0.000000  
1             0.000000  
2             0.000019  
3             0.000000  
4             0.000000

# JSON conversion

In [68]:
#Read data to json.
merged_json = json.loads(map_color_df.to_json())
#Convert to String like object.
json_data = json.dumps(merged_json)

In [69]:
json_data

'{"type": "FeatureCollection", "features": [{"id": "0", "type": "Feature", "properties": {"2018": 37172386.0, "Confirmed": 7.0, "ConfirmedDensityLog": 1.8831181137817415e-05, "ConfirmedDensityPerc": 0.01883118291088444, "Country Code": "AFG", "Country Name_x": "Afghanistan", "Deaths": 0.0, "DeathsDensityLog": 0.0, "DeathsDensityPerc": 0.0, "Recovered": 0.0, "RecoveredDensityLog": 0.0, "RecoveredDensityPerc": 0.0}, "geometry": {"type": "Polygon", "coordinates": [[[66.51860680528867, 37.36278432875879], [67.07578209825962, 37.35614390720929], [67.82999962755952, 37.144994004864685], [68.13556237170138, 37.02311513930431], [68.85944583524594, 37.344335842430596], [69.19627282092438, 37.15114350030743], [69.51878543485796, 37.60899669041342], [70.11657840361033, 37.58822276463209], [70.27057417184014, 37.735164699854025], [70.3763041523093, 38.13839590102752], [70.80682050973289, 38.486281643216415], [71.34813113799026, 38.25890534113216], [71.23940392444817, 37.953265082341886], [71.54191

# Plot map function

In [49]:
palette = brewer['PuBu'][9]
    #Reverse color order so that dark blue is highest obesity.
palette = palette[::-1]
print(palette)
print(palette[2::])

['#fff7fb', '#ece7f2', '#d0d1e6', '#a6bddb', '#74a9cf', '#3690c0', '#0570b0', '#045a8d', '#023858']
['#d0d1e6', '#a6bddb', '#74a9cf', '#3690c0', '#0570b0', '#045a8d', '#023858']


In [70]:
palette = cividis(256)
low = 0.0009
high = 38
color_mapper = LinearColorMapper(palette = palette, low = low, high = high, nan_color = '#d9d9d9', low_color='#d9d9d9')
color_bar = ColorBar(color_mapper=color_mapper, location = (0,0), orientation = 'horizontal')
geosource = GeoJSONDataSource(geojson=json_data)
p = figure(title = 'COVID-19 pandemic', plot_height = 600 , plot_width = 950, toolbar_location='below', toolbar_sticky=False, background_fill_color="#d9d9d9")
patches = p.patches('xs','ys', source = geosource, fill_color = {'field' :'ConfirmedDensityPerc', 'transform' : color_mapper}, line_color = 'black', line_width = 0.25, fill_alpha = 1)

show(p)

In [489]:
def plot_map(json_data, map_df):

    # Input GeoJSON source that contains features for plotting.
    geosource = GeoJSONDataSource(geojson=json_data)

    #Define a sequential multi-hue color palette.
    #palette = brewer['PuBu'][8]
    #Reverse color order so that dark blue is highest obesity.
    #palette = palette[::-1]
    #palette= palette[2::]
    
    #palette = cividis(9)
    #palette = gray(50)
    #palette = palette[::-1]
    #palette= palette[15::]
    
    #Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
    #color_mapper = LinearColorMapper(palette = palette, low = 0, high = 60, nan_color = '#d9d9d9')
    #color_mapper = LinearColorMapper(palette = palette, nan_color = '#d9d9d9')
    #color_mapper = LogColorMapper(palette = Viridis6, low = 0, high = 0.04, nan_color = '#d9d9d9')
    #log_color_mapper = LogColorMapper(palette = cividis(256), low = 0.0009, high = 38., nan_color = '#d9d9d9', low_color='#d9d9d9')
    palette = viridis(30)#brewer['PuBu'][9]#gray(21)
    palette = palette[::-1]
    palette= palette[14::] #[3::]
    low = 0.0009
    high = 38
    #color_mapper = LinearColorMapper(palette = palette, low = low, high = high, nan_color = '#d9d9d9', low_color='#d9d9d9')ghostwhite
    color_mapper = LogColorMapper(palette = palette, low =low, high = high, nan_color = 'white', low_color='white')
    
    #Create color bar. 
    #color_bar = ColorBar(color_mapper=color_mapper, label_standoff=8, width = 500, height = 20,
    #                     border_line_color=None, location = (0,0), orientation = 'horizontal')
    #color_bar = ColorBar(color_mapper=color_mapper, location = (0,0), orientation = 'horizontal')
    color_bar = ColorBar(color_mapper=color_mapper, location = (0,0), 
                         orientation = 'horizontal', ticker=LogTicker(), border_line_color=None, title='Confirmed cases per 100k inhabitants')
    #color_bar = ColorBar(color_mapper=color_mapper, location = (0,0), 
                         #orientation = 'horizontal', border_line_color=None)
    
    #Create figure object.
    p = figure(title = 'COVID-19 spread', plot_height = 600 , plot_width = 950, toolbar_location='below',
               toolbar_sticky=False, background_fill_color="lightsteelblue")#aliceblue")#lightskyblue")
    p.title.text_font = "helvetica"
    p.title.text_font_size = "20px"
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    
    #Add patch renderer to figure. 
    patches = p.patches('xs','ys', source = geosource, fill_color = {'field' :'ConfirmedDensityPerc', 'transform' : color_mapper},
         line_color = 'black', line_width = 0.25, fill_alpha = 0.5)
    #patches = p.patches('xs','ys', source = geosource,
     #     line_color = 'black', line_width = 0.25, fill_alpha = 1)
    
    #Specify figure layout.
    p.add_layout(color_bar, 'below')
    
    # create hoover
    hover = HoverTool(tooltips=[('Country', '@{Country Name_x}'), ('Population', '@2018'), ('Confirmed', '@Confirmed'),
                             ('Deaths', '@Deaths'), ('Recovered', '@Recovered'), ('Conf. per 100k', '@ConfirmedDensityPerc'),
                             ('Deaths per 100k', '@DeathsDensityPerc'), ('Recovered per 100k', '@RecoveredDensityPerc')], renderers=[patches])
    p.add_tools(hover)
    
    
     # Input coronavirus data
    pointsource = ColumnDataSource(map_df)
    
    # color palette
    palette_p = brewer['Reds'][9]
    palette_p = palette_p[::-1]
    palette_p[1::]
    color_mapper_p = LinearColorMapper(palette=palette_p, low=0, high=17)

     # add points virus
    point = p.circle('Long', 'Lat', source=pointsource, size='Size', color={'field': 'Size','transform': color_mapper_p}, 
                     fill_alpha=0.5, line_alpha=1)
    # create hoover
    hover_p = HoverTool(tooltips=[('Country', '@{Country/Region}'), ('Province', '@{Province/State}'), ('Confirmed', '@Confirmed'),
                            ('Deaths', '@Deaths'), ('Recovered', '@Recovered')], renderers=[point])
    p.add_tools(hover_p)
    
    
    def add_legend(location, orientation, side):
        legend = Legend(
            # TODO: title
            items=[("Nr. of confirmed cases", [point])],
            location=location, orientation=orientation,
            border_line_color="black",
            #title='Nr. confirmed cases',
            background_fill_alpha=0,
            border_line_alpha=0
        )
        p.add_layout(legend, side)

    # Add legends in names positions e.g. 'top_right', 'top_left' (see plot for all)
#     for location in LegendLocation:
#         add_legend(location, "vertical", "center")

    # Add legend at fixed positions
    add_legend('bottom_left', "horizontal", "center")
    
    
    #output_notebook()
    
    #Display figure.
    #show(p)
    

    return p

In [185]:
plot_map(json_data, map_df)

Figure(id='24972', ...)

# Prepare time series data frames

In [503]:
confirmed_df.reset_index().head()

Province/State Country/Region      Lat      Long  ...  2020-03-10 00:00:00  2020-03-11 00:00:00  2020-03-12 00:00:00  2020-03-13 00:00:00
0            NaN       Thailand  15.0000  101.0000  ...                   53                   59                   70                   75
1            NaN          Japan  36.0000  138.0000  ...                  581                  639                  639                  701
2            NaN      Singapore   1.2833  103.8333  ...                  160                  178                  178                  200
3            NaN          Nepal  28.1667   84.2500  ...                    1                    1                    1                    1
4            NaN       Malaysia   2.5000  112.5000  ...                  129                  149                  149                  197

[5 rows x 56 columns]

In [512]:
to_check =  confirmed_df.reset_index()
missing_countries_cov_ = to_check.loc[~to_check['Country/Region'].isin(df_pop['Country Name']), ['Country/Region']].values.flatten()
print(sorted(missing_countries_cov_))

['Brunei', 'Congo (Kinshasa)', 'Cruise Ship', 'Czechia', 'Egypt', 'French Guiana', 'Guadeloupe', 'Holy See', 'Iran', 'Korea, South', 'Martinique', 'Reunion', 'Russia', 'Slovakia', 'Taiwan*', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US', 'US',

In [266]:
def prepare_time_series_df(df):

    dff = df.copy().reset_index()
    
    dff.loc[dff['Country/Region']=='Brunei', ['Country/Region']]='Brunei Darussalam'
    dff.loc[dff['Country/Region']=='Congo (Kinshasa)', ['Country/Region']]='Congo, Dem. Rep.'
    dff.loc[dff['Country/Region']=='Czechia', ['Country/Region']]='Czech Republic'
    dff.loc[dff['Country/Region']=='French Guiana', ['Country/Region']]='French Guyana'
    dff.loc[dff['Country/Region']=='Egypt', ['Country/Region']]='Egypt, Arab Rep.'
    dff.loc[dff['Country/Region']=='Iran', ['Country/Region']]='Iran, Islamic Rep.'
    dff.loc[dff['Country/Region']=='Korea, South', ['Country/Region']]='Korea, Rep.'
    dff.loc[dff['Country/Region']=='Russia', ['Country/Region']]='Russian Federation'
    dff.loc[dff['Country/Region']=='Slovakia', ['Country/Region']]='Slovak Republic'
    dff.loc[dff['Country/Region']=='Taiwan*', ['Country/Region']]='Taiwan'
    dff.loc[dff['Country/Region']=='US', ['Country/Region']]='United States'
    
    dff = dff.groupby('Country/Region').sum()
    dff.reset_index(inplace = True)
    #print(dff.head())    
    
    diff_df = dff.copy()
    diff_df.drop(['Lat', 'Long'], axis=1, inplace=True)
    diff_df.sort_values(by='Country/Region', inplace=True)
    c_r=diff_df['Country/Region']
    diff_df = diff_df.diff(axis=1)
    diff_df.fillna(0, inplace=True)
    diff_df['Country/Region']=c_r
    diff_df.set_index('Country/Region', inplace=True, drop=True)
    diff_df = diff_df.T
    diff_df.columns.name = ""
    diff_df.index.name = "Date"
    diff_df.reset_index(inplace=True)
    #diff_df.set_index('Country/Region', drop=True)
    #diff_df = diff_df.T
    #diff_df.columns.name = ""
    #diff_df.index.name = "Date"
    #diff_df.reset_index(inplace=True)
      
    df_merged = pd.merge(dff, df_pop, left_on='Country/Region', right_on='Country Name', how='left')
    
    df_merged.loc[df_merged['Country/Region']=='Guadeloupe', ['2018']]=395700.
    df_merged.loc[df_merged['Country/Region']=='Holy See', ['2018']]= 1000.
    df_merged.loc[df_merged['Country/Region']=='Martinique', ['2018']]=376480.
    df_merged.loc[df_merged['Country/Region']=='Reunion', ['2018']]=859959.
    df_merged.loc[df_merged['Country/Region']=='Taiwan', ['2018']]=23216236.
    df_merged.loc[df_merged['Country/Region']=='Cruise Ship', ['2018']]=1000.
    df_merged.loc[df_merged['Country/Region']=='French Guyana', ['2018']]=255455.
    df_merged.loc[df_merged['Country/Region']=='Guadeloupe', ['Country Name']]='Guadeloupe'
    df_merged.loc[df_merged['Country/Region']=='Holy See', ['Country Name']]= 'Holy See'
    df_merged.loc[df_merged['Country/Region']=='Martinique', ['Country Name']]='Martinique'
    df_merged.loc[df_merged['Country/Region']=='Reunion', ['Country Name']]='Reunion'
    df_merged.loc[df_merged['Country/Region']=='Taiwan', ['Country Name']]='Taiwan'
    df_merged.loc[df_merged['Country/Region']=='Cruise Ship', ['Country Name']]='Cruise Ship'
    df_merged.loc[df_merged['Country/Region']=='French Guyana', ['Country Name']]='French Guyana'
    df_merged.loc[df_merged['Country/Region']=='Guadeloupe', ['Country Code']]='GLP'
    df_merged.loc[df_merged['Country/Region']=='Holy See', ['Country Code']]= 'VAT'
    df_merged.loc[df_merged['Country/Region']=='Martinique', ['Country Code']]='MTQ'
    df_merged.loc[df_merged['Country/Region']=='Reunion', ['Country Code']]='REU'
    df_merged.loc[df_merged['Country/Region']=='Taiwan', ['Country Code']]='TWN'
    df_merged.loc[df_merged['Country/Region']=='Cruise Ship', ['Country Code']]='cruise'
    df_merged.loc[df_merged['Country/Region']=='French Guyana', ['Country Code']]='GUF'
    
    
    df_merged['2018'] = df_merged['2018'].apply(lambda x: x/10000)
    for c in df_merged.columns[3:-3]:
        df_merged[c] = df_merged[c]/df_merged['2018']

    df_merged.drop(['Lat', 'Long', 'Country Name', 'Country Code', '2018'], axis=1, inplace=True)
    
    df_merged.set_index('Country/Region', inplace=True, drop=True)
    df_merged = df_merged.T
    df_merged.columns.name = ""
    df_merged.index.name = "Date"
    df_merged.reset_index(inplace=True)
    #df_merged.head(2)
    return df_merged, diff_df

In [267]:
confirmed_df_ts, confirmed_diff_ts= prepare_time_series_df(confirmed_df)
confirmed_diff_ts.head()

Date  Afghanistan  Albania  Algeria  Andorra  Antigua and Barbuda  \
0 2020-01-22          0.0      0.0      0.0      0.0                  0.0   
1 2020-01-23          0.0      0.0      0.0      0.0                  0.0   
2 2020-01-24          0.0      0.0      0.0      0.0                  0.0   
3 2020-01-25          0.0      0.0      0.0      0.0                  0.0   
4 2020-01-26          0.0      0.0      0.0      0.0                  0.0   

   Argentina  Armenia  Aruba  Australia  ...  Taiwan  Thailand  Togo  Tunisia  \
0        0.0      0.0    0.0        0.0  ...     0.0       0.0   0.0      0.0   
1        0.0      0.0    0.0        0.0  ...     0.0       1.0   0.0      0.0   
2        0.0      0.0    0.0        0.0  ...     2.0       2.0   0.0      0.0   
3        0.0      0.0    0.0        0.0  ...     0.0       2.0   0.0      0.0   
4        0.0      0.0    0.0        4.0  ...     1.0       1.0   0.0      0.0   

   Turkey  Ukraine  United Arab Emirates  United Kingdom  United States  \
0     0.0      0.0                   0.0             0.0            0.0   
1     0.0      0.0                   0.0             0.0            0.0   
2     0.0      0.0                   0.0             0.0            1.0   
3     0.0      0.0                   0.0             0.0            0.0   
4     0.0      0.0                   0.0             0.0            3.0   

   Vietnam  
0      0.0  
1      2.0  
2      0.0  
3      0.0  
4      0.0  

[5 rows x 126 columns]

In [268]:
confirmed_df_ts.head()

Date  Afghanistan  Albania  Algeria  Andorra  Antigua and Barbuda  \
0 2020-01-22          0.0      0.0      0.0      0.0                  0.0   
1 2020-01-23          0.0      0.0      0.0      0.0                  0.0   
2 2020-01-24          0.0      0.0      0.0      0.0                  0.0   
3 2020-01-25          0.0      0.0      0.0      0.0                  0.0   
4 2020-01-26          0.0      0.0      0.0      0.0                  0.0   

   Argentina  Armenia  Aruba  Australia  ...    Taiwan  Thailand  Togo  \
0        0.0      0.0    0.0     0.0000  ...  0.000431  0.000288   0.0   
1        0.0      0.0    0.0     0.0000  ...  0.000431  0.000432   0.0   
2        0.0      0.0    0.0     0.0000  ...  0.001292  0.000720   0.0   
3        0.0      0.0    0.0     0.0000  ...  0.001292  0.001008   0.0   
4        0.0      0.0    0.0     0.0016  ...  0.001723  0.001152   0.0   

   Tunisia  Turkey  Ukraine  United Arab Emirates  United Kingdom  \
0      0.0     0.0      0.0                   0.0             0.0   
1      0.0     0.0      0.0                   0.0             0.0   
2      0.0     0.0      0.0                   0.0             0.0   
3      0.0     0.0      0.0                   0.0             0.0   
4      0.0     0.0      0.0                   0.0             0.0   

   United States   Vietnam  
0       0.000031  0.000000  
1       0.000031  0.000209  
2       0.000061  0.000209  
3       0.000061  0.000209  
4       0.000153  0.000209  

[5 rows x 126 columns]

In [321]:
recovered_df_ts, recovered_diff_ts= prepare_time_series_df(recovered_df)

In [322]:
deaths_df_ts, deaths_diff_ts= prepare_time_series_df(deaths_df)

In [238]:
df_confirmed_sum = confirmed_df.groupby('Country/Region').sum()
df_confirmed_sum = df_confirmed_sum.sum(axis=1).sort_values(ascending=False)
df_confirmed_sum.head(20)

Country/Region
China             2719449
Italy               96946
Korea, South        96672
Iran                75645
Cruise Ship         19172
France              15660
Spain               15128
Germany             14611
US                   9163
Japan                8380
Switzerland          4492
Singapore            3683
United Kingdom       3643
Norway               3574
Netherlands          3274
Sweden               3214
Denmark              2347
Belgium              2293
Malaysia             1777
Austria              1745
dtype: int64

In [293]:
countries = ['China', 'Italy', 'Korea, Rep.', 'Iran, Islamic Rep.', 'France', 'Spain', 'Germany', 'United States', 'Switzerland', 'United Kingdom', 'Japan']

In [286]:
palette = Category10[10]
print(palette)

['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2', '#7f7f7f', '#bcbd22', '#17becf']


In [338]:
confirmed_df_ts.shape

(52, 126)

In [355]:
import time
from datetime import datetime as dt

hubei_ld = dt.strptime('Jan 23 2020', '%b %d %Y')
italy_ld = dt.strptime('Mar 09 2020', '%b %d %Y')
print(hubei_ld)

2020-01-23 00:00:00


In [490]:
def plot_time_series2(line_df, countries, which):
    # print(which)
    TOOLS = 'pan,box_zoom,reset,wheel_zoom'

    cds = ColumnDataSource(line_df)
    #p = figure(title=f"{which} cases per 100k inhabitants", y_axis_type="log", 
    #            x_axis_type='datetime',  plot_height=400, plot_width=950, tools=TOOLS, toolbar_location='below', toolbar_sticky=False)  # background_fill_color="silver"
    p = figure(title=f"{which} cases per 100k inhabitants", y_axis_type="log", 
               x_axis_type='datetime')  # background_fill_color="silver"
    p.title.text_font = "helvetica"
    p.title.text_font_size = "20px"
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None

#     palette = brewer['RdBu'][11]
#     palette = palette[::-1]

    palette = Category20[11]  # brewer['PuBu'][9]#gray(21)
    #palette = palette[::-1]
    items = []
    for i, country in enumerate(countries):
        # print(country)
        c = p.line('Date', country,
                   line_color=palette[i], line_width=2.5, source=cds)
        point = p.circle('Date', country,
                   line_color=palette[i], fill_color=palette[i], fill_alpha=0, size=7, source=cds)
        hover = HoverTool(tooltips=[("Date", "@Date{%F}"),
                                    (f"{which} cases per 100k inhabitants {country}", "$y")], formatters={
            '@Date': 'datetime'  # use 'datetime' formatter for '@date' field
        }, renderers=[c])
        items.append(LegendItem(label=country, renderers=[point, c]))
        p.add_tools(hover)

    china_lockdown = Span(location=hubei_ld,
                              dimension='height', line_color='black',
                              line_dash='dashed', line_width=1.5)
    italy_lockdown = Span(location=italy_ld,
                              dimension='height', line_color='black',
                              line_dash='dashed', line_width=1.5)
    
    p.add_layout(china_lockdown)
    p.add_layout(italy_lockdown)
    
    china_lockdown_citation = Label(x=hubei_ld, y=0.03, x_units='data', y_units='data',
                                     text='Hubei lockdown', render_mode='canvas',
                                     border_line_color='white', border_line_alpha=0,
                                     background_fill_color='white', background_fill_alpha=0, angle_units='deg', angle=90)
    p.add_layout(china_lockdown_citation)
    italy_lockdown_citation = Label(x=italy_ld, y=2e-5, x_units='data', y_units='data',
                                     text='Italy lockdown', render_mode='canvas',
                                     border_line_color='white', border_line_alpha=0,
                                     background_fill_color='white', background_fill_alpha=0, angle_units='deg', angle=90)
    p.add_layout(italy_lockdown_citation)
        
    legend = Legend(items=items, location=(0, -30))
    p.add_layout(legend, 'right')

    p.legend.location = "top_left"
    p.legend.click_policy = "hide"
    p.legend.background_fill_alpha = 0
    p.legend.border_line_alpha = 0
    p.legend.glyph_height = 10
    p.legend.glyph_width = 10
    p.legend.label_text_font_size = '10pt'
    
    p.xaxis.ticker.desired_num_ticks = 10

    p.xaxis.axis_label = 'Date'
    #p.yaxis.axis_label = 'Counts/100k inhabitants'
    p.yaxis.axis_label = ''
    p.y_range=Range1d(1e-5, 10)

# Display figure inline in Jupyter Notebook.
# output_notebook()
# Display figure.
    #show(p)

    return p

In [393]:
plot_time_series2(confirmed_df_ts, countries, 'Confirmed')

Figure(id='89963', ...)

In [394]:
plot_time_series2(deaths_df_ts, countries, 'Death')

Figure(id='91803', ...)

In [395]:
plot_time_series2(recovered_df_ts, countries, 'Recovered')

Figure(id='93663', ...)

# Dashboard

In [491]:
grid = pn.GridSpec(sizing_mode='stretch_both', max_height=1300)
header = """# COVID-19 Dashboard
Data source [Johns Hopkins CSSE](https://github.com/CSSEGISandData/COVID-19)<br />
Inspired by [COVID-19 Dashboard](https://www.arcgis.com/apps/opsdashboard/index.html#/bda7594740fd40299423467b48e9ecf6)"""

total_confirmed = f"Total Confirmed\n# {confirmed_df.iloc[:,-1].sum()}"
total_deaths   = f"Total Deaths\n# {deaths_df.iloc[:,-1].sum()}"
total_recovered = f"Total Recovered\n# {recovered_df.iloc[:,-1].sum()}"
grid[0,    0:12]   = pn.pane.Markdown(header)
grid[1:8,  0:9]   = pn.Row(plot_map(json_data, map_df))
grid[1,    9]     = pn.pane.Markdown(total_confirmed)
grid[1,    10]     = pn.pane.Markdown(total_deaths)
grid[1,    11]     = pn.pane.Markdown(total_recovered)
grid[2:8,  9]     = pn.Column(pn.pane.DataFrame(confirmed_ser), height=400, scroll=True)
grid[2:8,  10]     = pn.Column(pn.pane.DataFrame(deaths_ser), height=400, scroll=True)
grid[2:8,  11]     = pn.Column(pn.pane.DataFrame(recovered_ser), height=400, scroll=True)
           #         pn.Row(plot_time_series2(confirmed_df_ts, countries, 'Confirmed'), plot_time_series2(deaths_df_ts, countries, 'Deaths'), plot_time_series2(recovered_df_ts, countries, 'Recovered'))
grid[8:11, 0:4]   = pn.Row(plot_time_series2(confirmed_df_ts, countries, 'Confirmed'))
grid[8:11, 4:8]   = pn.Row(plot_time_series2(deaths_df_ts, countries, 'Deaths'))
grid[8:11, 8:12]   = pn.Row(plot_time_series2(recovered_df_ts, countries, 'Recovered'))

#grid[3:5, 4:6] = plot_time_series2(confirmed_df_ts, countries, 'Confirmed')

grid.servable()

GridSpec(max_height=1300, sizing_mode='stretch_both')
    [0] Markdown(str, sizing_mode='stretch_both')
    [1] Row(sizing_mode='stretch_both')
        [0] Bokeh(Figure)
    [2] Markdown(str, sizing_mode='stretch_both')
    [3] Markdown(str, sizing_mode='stretch_both')
    [4] Markdown(str, sizing_mode='stretch_both')
    [5] Column(height=400, scroll=True, sizing_mode='stretch_both')
        [0] DataFrame(Series)
    [6] Column(height=400, scroll=True, sizing_mode='stretch_both')
        [0] DataFrame(Series)
    [7] Column(height=400, scroll=True, sizing_mode='stretch_both')
        [0] DataFrame(Series)
    [8] Row(sizing_mode='stretch_both')
        [0] Bokeh(Figure)
    [9] Row(sizing_mode='stretch_both')
        [0] Bokeh(Figure)
    [10] Row(sizing_mode='stretch_both')
        [0] Bokeh(Figure)

# Diff vs Time

In [413]:
def plot_time_diff(line_df, countries, which):
    TOOLS = 'pan,box_zoom,reset,wheel_zoom'

    cds = ColumnDataSource(line_df)

    p = figure(title=f"{which} cases per 100k inhabitants", y_axis_type="linear", 
               x_axis_type='datetime', plot_height=400, plot_width=950, tools=TOOLS, toolbar_location='below', toolbar_sticky=False)  # background_fill_color="silver",
    p.title.text_font = "helvetica"
    p.title.text_font_size = "20px"
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None

#     palette = brewer['RdBu'][11]
#     palette = palette[::-1]

    palette = Category20[11]  # brewer['PuBu'][9]#gray(21)
    #palette = palette[::-1]
    items = []
    for i, country in enumerate(countries):
        # print(country)
        c = p.line('Date', country,
                   line_color=palette[i], line_width=2.5, source=cds)
        point = p.circle('Date', country,
                   line_color=palette[i], fill_color=palette[i], fill_alpha=0, size=7, source=cds)
        hover = HoverTool(tooltips=[("Date", "@Date{%F}"),
                                    (f"{which} cases per 100k inhabitants {country}", "$y")], formatters={
            '@Date': 'datetime'  # use 'datetime' formatter for '@date' field
        }, renderers=[c])
        items.append(LegendItem(label=country, renderers=[point, c]))
        p.add_tools(hover)

    china_lockdown = Span(location=hubei_ld,
                              dimension='height', line_color='black',
                              line_dash='dashed', line_width=1.5)
    italy_lockdown = Span(location=italy_ld,
                              dimension='height', line_color='black',
                              line_dash='dashed', line_width=1.5)
    
    p.add_layout(china_lockdown)
    p.add_layout(italy_lockdown)
    
    china_lockdown_citation = Label(x=hubei_ld, y=0.03, x_units='data', y_units='data',
                                     text='Hubei lockdown', render_mode='canvas',
                                     border_line_color='white', border_line_alpha=0,
                                     background_fill_color='white', background_fill_alpha=0, angle_units='deg', angle=90)
    p.add_layout(china_lockdown_citation)
    italy_lockdown_citation = Label(x=italy_ld, y=2e-5, x_units='data', y_units='data',
                                     text='Italy lockdown', render_mode='canvas',
                                     border_line_color='white', border_line_alpha=0,
                                     background_fill_color='white', background_fill_alpha=0, angle_units='deg', angle=90)
    p.add_layout(italy_lockdown_citation)
        
    legend = Legend(items=items, location=(0, -30))
    p.add_layout(legend, 'right')

    p.legend.location = "top_left"
    p.legend.click_policy = "hide"
    p.legend.background_fill_alpha = 0
    p.legend.border_line_alpha = 0
    p.legend.glyph_height = 10
    p.legend.glyph_width = 10
    p.legend.label_text_font_size = '10pt'
    
    p.xaxis.ticker.desired_num_ticks = 20

    p.xaxis.axis_label = 'Date'
    p.yaxis.axis_label = 'Counts/100k inhabitants'
    p.y_range=Range1d(1e-5, 10)

# Display figure inline in Jupyter Notebook.
# output_notebook()
# Display figure.
    show(p)

    return p

In [414]:
plot_time_diff(confirmed_diff_ts, countries, 'Confirmed')

Figure(id='99393', ...)

In [415]:
confirmed_diff_ts['Japan'].values

array([  0.,  -1.,   1.,   0.,   2.,   0.,   3.,   0.,   4.,   4.,   5.,
         0.,   0.,   2.,   0.,  23., -20.,   0.,   1.,   0.,   0.,   2.,
         0.,   1.,  14.,  16.,   7.,   8.,  10.,  10.,  11.,  17.,  25.,
        12.,  11.,  19.,  25.,  14.,  13.,  15.,  18.,  19.,  38.,  29.,
        60.,  41.,  41.,   9.,  70.,  58.,   0.,  62.])

In [416]:
confirmed_df_ts['Japan'].values

array([1.58066405e-04, 7.90332026e-05, 1.58066405e-04, 1.58066405e-04,
       3.16132811e-04, 3.16132811e-04, 5.53232418e-04, 5.53232418e-04,
       8.69365229e-04, 1.18549804e-03, 1.58066405e-03, 1.58066405e-03,
       1.58066405e-03, 1.73873046e-03, 1.73873046e-03, 3.55649412e-03,
       1.97583007e-03, 1.97583007e-03, 2.05486327e-03, 2.05486327e-03,
       2.05486327e-03, 2.21292967e-03, 2.21292967e-03, 2.29196288e-03,
       3.39842771e-03, 4.66295896e-03, 5.21619137e-03, 5.84845700e-03,
       6.63878902e-03, 7.42912105e-03, 8.29848628e-03, 9.64205072e-03,
       1.16178808e-02, 1.25662792e-02, 1.34356444e-02, 1.49372753e-02,
       1.69131054e-02, 1.80195702e-02, 1.90470018e-02, 2.02324999e-02,
       2.16550975e-02, 2.31567284e-02, 2.61599901e-02, 2.84519529e-02,
       3.31939451e-02, 3.64343064e-02, 3.96746677e-02, 4.03859665e-02,
       4.59182907e-02, 5.05022165e-02, 5.05022165e-02, 5.54022750e-02])

In [419]:
confirmed_df.head()

2020-01-22  2020-01-23  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000           2           3   
               Japan          36.0000 138.0000           2           1   
               Singapore      1.2833  103.8333           0           1   
               Nepal          28.1667 84.2500            0           0   
               Malaysia       2.5000  112.5000           0           0   

                                                2020-01-24  2020-01-25  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000           5           7   
               Japan          36.0000 138.0000           2           2   
               Singapore      1.2833  103.8333           3           3   
               Nepal          28.1667 84.2500            0           1   
               Malaysia       2.5000  112.5000           0           3   

                                                2020-01-26  2020-01-27  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000           8           8   
               Japan          36.0000 138.0000           4           4   
               Singapore      1.2833  103.8333           4           5   
               Nepal          28.1667 84.2500            1           1   
               Malaysia       2.5000  112.5000           4           4   

                                                2020-01-28  2020-01-29  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000          14          14   
               Japan          36.0000 138.0000           7           7   
               Singapore      1.2833  103.8333           7           7   
               Nepal          28.1667 84.2500            1           1   
               Malaysia       2.5000  112.5000           4           7   

                                                2020-01-30  2020-01-31  ...  \
Province/State Country/Region Lat     Long                              ...   
NaN            Thailand       15.0000 101.0000          14          19  ...   
               Japan          36.0000 138.0000          11          15  ...   
               Singapore      1.2833  103.8333          10          13  ...   
               Nepal          28.1667 84.2500            1           1  ...   
               Malaysia       2.5000  112.5000           8           8  ...   

                                                2020-03-04  2020-03-05  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000          43          47   
               Japan          36.0000 138.0000         331         360   
               Singapore      1.2833  103.8333         110         117   
               Nepal          28.1667 84.2500            1           1   
               Malaysia       2.5000  112.5000          50          50   

                                                2020-03-06  2020-03-07  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000          48          50   
               Japan          36.0000 138.0000         420         461   
               Singapore      1.2833  103.8333         130         138   
               Nepal          28.1667 84.2500            1           1   
               Malaysia       2.5000  112.5000          83          93   

                                                2020-03-08  2020-03-09  \
Province/State Country/Region Lat     Long                               
NaN            Thailand       15.0000 101.0000          50          50   
               Japan          36.0000 138.0000         502         511   
               Singapore      1.2833  103.8333         150         150   
          

In [424]:
testdf = confirmed_df.reset_index()
testdf.loc[testdf['Country/Region']=='Japan'].values

array([[nan, 'Japan', 36.0, 138.0, 2, 1, 2, 2, 4, 4, 7, 7, 11, 15, 20,
        20, 20, 22, 22, 45, 25, 25, 26, 26, 26, 28, 28, 29, 43, 59, 66,
        74, 84, 94, 105, 122, 147, 159, 170, 189, 214, 228, 241, 256,
        274, 293, 331, 360, 420, 461, 502, 511, 581, 639, 639, 701]],
      dtype=object)

In [425]:
testdf.loc[testdf['Country/Region']=='Italy'].values

array([[nan, 'Italy', 43.0, 12.0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 2, 2, 2,
        2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 20, 62, 155,
        229, 322, 453, 655, 888, 1128, 1694, 2036, 2502, 3089, 3858,
        4636, 5883, 7375, 9172, 10149, 12462, 12462, 17660]], dtype=object)

In [428]:
display(testdf.loc[testdf['Country/Region']=='China', []])

Province/State Country/Region      Lat      Long  2020-01-22 00:00:00  \
156           Hubei          China  30.9756  112.2707                  444   
160       Guangdong          China  23.3417  113.4244                   26   
161           Henan          China  33.8820  113.6140                    5   
162        Zhejiang          China  29.1832  120.0934                   10   
163           Hunan          China  27.6104  111.7088                    4   
164           Anhui          China  31.8257  117.2264                    1   
165         Jiangxi          China  27.6140  115.7221                    2   
166        Shandong          China  36.3427  118.1498                    2   
168         Jiangsu          China  32.9711  119.4550                    1   
169       Chongqing          China  30.0572  107.8740                    6   
170         Sichuan          China  30.6171  102.7103                    5   
171    Heilongjiang          China  47.8620  127.7615                    0   
173         Beijing          China  40.1824  116.4142                   14   
174        Shanghai          China  31.2020  121.4491                    9   
175           Hebei          China  39.5490  116.1306                    1   
176          Fujian          China  26.0789  117.9874                    1   
177         Guangxi          China  23.8298  108.7881                    2   
178         Shaanxi          China  35.1917  108.8701                    0   
179          Yunnan          China  24.9740  101.4870                    1   
180          Hainan          China  19.1959  109.7453                    4   
181         Guizhou          China  26.8154  106.8748                    1   
182         Tianjin          China  39.3054  117.3230                    4   
183          Shanxi          China  37.5777  112.2922                    1   
184           Gansu          China  37.8099  101.0583                    0   
185       Hong Kong          China  22.3000  114.2000                    0   
186        Liaoning          China  41.2956  122.6085                    2   
187           Jilin          China  43.6661  126.1923                    0   
189        Xinjiang          China  41.1129   85.2401                    0   
190  Inner Mongolia          China  44.0935  113.9448                    0   
191         Ningxia          China  37.2692  106.1655                    1   
195         Qinghai          China  35.7452   95.9956                    0   
196           Macau          China  22.1667  113.5500                    1   
204           Tibet          China  31.6927   88.0924                    0   

     2020-01-23 00:00:00  2020-01-24 00:00:00  2020-01-25 00:00:00  \
156                  444                  549                  761   
160                   32                   53                   78   
161                    5                    9                   32   
162                   27                   43                   62   
163                    9                   24                   43   
164                    9                   15                   39   
165                    7                   18                   18   
166                    6                   15                   27   
168                    5                    9                   18   
169                    9                   27                   57   
170                    8                   15                   28   
171                    2                    4                    9   
173                   22                   36                   41   
174                   16                   20                   33   
175                    1                    2                    8   
176                    5                   10                   18   
177                    5                   23                   23   
178                    3                    5                   15   
179                   